<a href="https://colab.research.google.com/github/barrylunemann/mapping/blob/main/geojson_timelapse_heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
"""
Created on Tue May 10 12:39:56 2022

@author: BarryLunemann
"""
!pip install geopandas
import folium
import pandas as pd
import numpy as np
import geopandas as gpd
import branca.colormap as cm
from folium.plugins import TimestampedGeoJson
from branca.element import Template, MacroElement
from os import chdir
import datetime
from matplotlib import colors

     |████████████████████████████████| 1.0 MB 4.2 MB/s 
     |████████████████████████████████| 16.7 MB 53.5 MB/s 
     |████████████████████████████████| 6.3 MB 55.6 MB/s 


In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
# User inputs
service_line_column_name = 'SPORT'
# if you want to include all then set service_line = ''
service_line = 'Baseball'
# Name of number column
number_column_name = 'REGISTRATIONS'
# Output File Name
output_file_name = 'Output File'

In [4]:
# Add your data here.
# Format Column Names Required (Zip Code, Date, Number) #Cleaning this for SE data
number_df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/Data/MNRegMay21-Apr22.csv',
                        dtype={'POSTAL CODE': str})

In [5]:
# Renaming Zip Code Column if needed
number_df.rename(columns={'POSTAL CODE': 'Zip Code'}, inplace=True)

In [6]:
# Rename Date Column if Needed
number_df.rename(columns={'Days in date_range': 'Date',
                         number_column_name: 'Visits'}, inplace=True)

In [7]:
# Drop if Missing Date
number_df = number_df.dropna(subset=['Date'])

In [8]:
# Cleanup zip codes to make sure they have 5 digits
number_df = number_df.dropna(subset=['Zip Code'])

# Function to cleanup Zip Codes. If it errors on the zip it will drop it.
def fix_zip_codes(zip_number):
    try:
        if len(zip_number) >= 5:
            output_str = zip_number[:5]
            int(output_str)
            return(output_str)
        elif len(zip_number) < 5:
            output_str = str((5-len(str(zip_number))) * '0') + zip_number
            int(output_str)
            return(output_str)
        else:
            return(zip_number)
                
    except Exception:
        return('0000A')
    
    
number_df['Zip Code'] = number_df.apply(lambda row:
                                        fix_zip_codes(row['Zip Code']),
                                        axis=1)
number_df = number_df[number_df['Zip Code'] != '0000A'].reset_index(drop=True)

In [9]:
# Pulling zip code shape files
geo_zip = gpd.read_file(r"/content/drive/MyDrive/Colab Notebooks/Data/Zip Code Shape Data/cb_2018_us_zcta510_500k.shp")
geo_zip.rename(columns={'ZCTA5CE10': 'Zip Code'}, inplace=True)

In [10]:
# Convert Date field to dates
number_df['Date'] = pd.to_datetime(number_df['Date'], errors='coerce')

number_df['Date'
          ] = number_df.apply(lambda row:
                              datetime.date(int(row['Date'].year),
                                            int(row['Date'].month),
                                            int(row['Date'].day)),
                              axis=1)
number_df['Datetime'
          ] = number_df.apply(lambda row:
                              datetime.datetime(int(row['Date'].year),
                                            int(row['Date'].month),
                                            int(row['Date'].day),
                                            0,0,0),
                              axis=1)

In [11]:
# Break out data by week and merge back to main file
number_df['Week Number'] = number_df['Datetime'].dt.week
number_df['Year'] = number_df.apply(lambda row:
                                    row['Date'].year,
                                    axis=1)

week_start = number_df.loc[:, ['Date', 'Week Number', 'Year']].drop_duplicates().sort_values(['Year', 'Week Number', 'Date'])
week_start.drop_duplicates(subset=['Week Number', 'Year'],
                           keep='first',
                           inplace=True)
week_start.rename(columns={'Date': 'Week Start'}, inplace=True)
week_start['Week Start'] = week_start.apply(lambda row:
                                            datetime.datetime(row['Week Start'].year,
                                                            row['Week Start'].month,
                                                            row['Week Start'].day,
                                                            0, 0, 0),
                                            axis=1)
number_df = number_df.merge(week_start, on=['Week Number', 'Year'], how='left')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.
  


In [12]:
# Converting to epoch time to make folium happy (this might not be necessary- for future review)
number_df['Week Start'] = number_df.apply(lambda row:
                                          (row['Week Start'] - datetime.datetime(1970,1,1)).total_seconds(),
                                          axis=1)

In [13]:
# Removing service lines you don't want
if service_line != '':
    number_df = number_df[number_df[service_line_column_name] == service_line]
else:
    number_df[service_line_column_name] = service_line

In [14]:
# Group together if not already (original data set I used had a row for every visit, so the commented out section isn't needed if it is already grouped)
# I am grouping it to the weekly level
number_df = number_df.loc[:, ['Week Start',
                              'Zip Code',
                              service_line_column_name,
                              'Visits']]
# number_df['Visits'] = 1
number_df = number_df.groupby(by=['Week Start',
                                  'Zip Code',
                                  service_line_column_name],
                              as_index=False).sum()

In [15]:
# Merging with zip code shape file and dropping blanks
cleaned_df = geo_zip.merge(number_df, on='Zip Code', how='left')
cleaned_df = cleaned_df.dropna(subset=[service_line_column_name])

In [16]:
# Creating list of dates to iterate through
date_list_final = cleaned_df.loc[:, 'Week Start'].drop_duplicates().to_list()

In [17]:
# Break out zip codes with Multiple Polygons.
# The whole zip code will be mapped, but in the mapping data,
# they will be 1 zip code with rows for each of the polygons
cleaned_df = cleaned_df.explode(ignore_index=True, index_parts=False)
cleaned_df = cleaned_df.reset_index(drop=True)

In [18]:
# Primary function that puts the data into a format that can be pulled into folium
def create_geojson_features(df, num_col_name, date_list):
    # Creating the heatmap colors
    colormap = cm.linear.RdYlGn_11.colors
    
    # Creating buckets for the heatmap colors
    max_number = df.Visits.max()
    min_number = df.Visits.min()
    difference = max_number - min_number
    buckets = int(difference / 10)
    index_list = []
    for x in range(11):
        index_list.append(int(max(0, min_number + buckets * x)))

    # Creating a dictionary look up for color breakdown.
    color_dict = {}
    counter_dict = 1
    for iter in colormap:
        color_dict[index_list[-counter_dict]] = (colors.to_hex(iter))
        counter_dict += 1

    # primary feature list that will be returned at the end of the function 
    features = []
    
    # Creating a list of all numbers 
    unique_visits = df.loc[:, 'Visits'].drop_duplicates().to_list()
    
    # iterating through the number
    for visit_iter in unique_visits:
        lst = np.asarray(index_list)
        idx = (np.abs(lst - visit_iter)).argmin()
        visit_color = color_dict[lst[idx]]
        
        # iterating through the date list passed to the function
        for date_iter in date_list:
            coordinates = []
            timestamps = []
            visits=[]
            real_timestamp = []
            for geometry,start_time,zip_code,visits in zip(df['geometry'],
                                                           df['Week Start'],
                                                           df['Zip Code'],
                                                           df['Visits']):

                if (visit_iter == visits and
                    date_iter == start_time):

                    temp_poly = (list(geometry.exterior.coords))
                    coordinates.append(temp_poly)
                    # timestamps.append(str(datetime.datetime(start_time.year,
                    #                                         start_time.month,
                    #                                         start_time.day,
                    #                                         0, 0, 0)))
                    timestamps.append(str(datetime.datetime.fromtimestamp(start_time)))

                    real_timestamp.append(start_time)


            if len(coordinates) > 0:
                feature = {
                            'type': 'Feature',
                            'geometry': {
                                        'type':'Polygon',
                                        'coordinates': coordinates
                                        },
                            'properties': {'times': timestamps,
                                          'style': {"color": visit_color,
                                                    "stroke-width": 1,
                                                    'fillColor': visit_color,
                                                    'fillOpacity': 0.7
                                                    }
                                          }
                            }

                features.append(feature)
        # # counter += 1

    # features.append(feature)
    return(features, color_dict)

In [19]:
# Test Run with less data
# features, color_map = create_geojson_features(cleaned_df.head(250), number_column_name, date_list_final)

In [20]:
# Call Primary Function
features, color_map = create_geojson_features(cleaned_df, number_column_name, date_list_final)

In [32]:
# Creating map and setting up starting location and how far it is zoomed out.
kol = folium.Map(location=[45.942399690174064, -94.49636635673328],
                 tiles='openstreetmap',
                 zoom_start=7)

In [33]:
# Creating all the fun stuff and adding to the map.
TimestampedGeoJson({
        'type': 'FeatureCollection'
        , 'features': features}
        , period='P7D'
        , add_last_point=False
        , auto_play=True
        , loop=False
        , max_speed=30
        , loop_button=True
        , date_options='YYYY/MM/DD'
        , time_slider_drag_update=True
        , duration='P6D'
    ).add_to(kol)

In [35]:
# Creating a legend so you know what the colors mean
color_list = []
for iter in color_map.keys():
    color_list.append(iter)

template = """
        {% macro html(this, kwargs) %}
        
        <!doctype html>
        <html lang="en">
        <head>
          <meta charset="utf-8">
          <meta name="viewport" content="width=device-width, initial-scale=1">
          <title>jQuery UI Draggable - Default functionality</title>
          <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">
        
          <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
          <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
          
          <script>
          $( function() {
            $( "#maplegend" ).draggable({
                            start: function (event, ui) {
                                $(this).css({
                                    right: "auto",
                                    top: "auto",
                                    bottom: "auto"
                                });
                            }
                        });
        });
        
          </script>
        </head>
        <body>
        
         
        <div id='maplegend' class='maplegend' 
            style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
             border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
             
        <div class='legend-title'>Heatmap Legend</div>
        <div class='legend-scale'>
          <ul class='legend-labels'>
            <li><span style='background:""" + color_map[color_list[0]] + """;opacity:0.7;'></span>"""  + str(color_list[0]) + """ or higher</li>
            <li><span style='background:""" + color_map[color_list[1]] + """;opacity:0.7;'></span>""" + str(color_list[1]) + ' to ' + str(color_list[0]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[2]] + """;opacity:0.7;'></span>""" + str(color_list[2]) + ' to ' + str(color_list[1]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[3]] + """;opacity:0.7;'></span>""" + str(color_list[3]) + ' to ' + str(color_list[2]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[4]] + """;opacity:0.7;'></span>""" + str(color_list[4]) + ' to ' + str(color_list[3]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[5]] + """;opacity:0.7;'></span>""" + str(color_list[5]) + ' to ' + str(color_list[4]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[6]] + """;opacity:0.7;'></span>""" + str(color_list[6]) + ' to ' + str(color_list[5]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[7]] + """;opacity:0.7;'></span>""" + str(color_list[7]) + ' to ' + str(color_list[6]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[8]] + """;opacity:0.7;'></span>""" + str(color_list[8]) + ' to ' + str(color_list[7]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[9]] + """;opacity:0.7;'></span>""" + str(color_list[9]) + ' to ' + str(color_list[8]-1) + """</li>
            <li><span style='background:""" + color_map[color_list[10]] + """;opacity:0.7;'></span>0 to """ + str(color_list[9]-1) + """</li>
          </ul>
        </div>
        </div>

        </body>
        </html>
        
        <style type='text/css'>
          .maplegend .legend-title {
            text-align: left;
            margin-bottom: 5px;
            font-weight: bold;
            font-size: 90%;
            }
          .maplegend .legend-scale ul {
            margin: 0;
            margin-bottom: 5px;
            padding: 0;
            float: left;
            list-style: none;
            }
          .maplegend .legend-scale ul li {
            font-size: 80%;
            list-style: none;
            margin-left: 0;
            line-height: 18px;
            margin-bottom: 2px;
            }
          .maplegend ul.legend-labels li span {
            display: block;
            float: left;
            height: 16px;
            width: 30px;
            margin-right: 5px;
            margin-left: 0;
            border: 1px solid #999;
            }
          .maplegend .legend-source {
            font-size: 80%;
            color: #777;
            clear: both;
            }
          .maplegend a {
            color: #777;
            }
        </style>
        {% endmacro %}"""

macro = MacroElement()
macro._template = Template(template)

kol.get_root().add_child(macro)

In [24]:
# Saving resulting map
kol.save(output_file_name+'.html')